# CARGANDO EL DATASET
* Importamos la librería para cargar la información previamente scrapeada de Maldita.es.
* 1224 noticias actualmente


In [58]:
import pickle

In [59]:
infile = open("Maldita_Dataset_02-07-2020",'rb')
dataset = pickle.load(infile)
len(dataset)

1224

# IMPORTING LIBRARIES
* Imports to preprocess the artcicles.

In [96]:
# -*- coding: utf-8 -*-
import re, string, unicodedata
import nltk
from nltk.tokenize import word_tokenize 
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from collections import Counter
from collections import defaultdict
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np
import spacy
from spacy.lang.es.stop_words import STOP_WORDS

In [97]:
#De los diccionarios de articulos ** me quedo solo con el contenido de x articulos del dataset y los introduzco en una lista
#de contenidos.
# **article = {"Title": title, "Publication_date": date, "Content": content, "URL": url, "Fuente": "Maldita.es"}
content_list = []
for a in dataset[:2]:
    content_list.append(a['Content'])

In [98]:
print(dataset[43])

{'Title': 'No, esta foto de una mujer abrazando a una agente de policía no ha sido tomada ni en el barrio de Salamanca de Madrid ni durante la crisis del coronavirus: fue en Barcelona en 2017', 'Publication_date': '16/05/2020', 'Content': 'Está circulando una foto en la que una mujer, que lleva una bandera de España, abraza a una agente de policía. Se comparte con mensajes como "Aquí una clara imagen de la policía repartiendo porrazos en el barrio de Salamanca". No obstante, es un bulo que esta imagen haya sido tomada en este barrio madrileño o que sea actual. Fue tomada durante la manifestación a favor de la unidad de España del 8 de octubre de 2017 en Barcelona. La Sexta emitió esta imagen el 8 de octubre de 2017, cuando en la manifestación a favor de la unidad de España de Barcelona algunas personas mostraron su afecto a agentes de la policía. Entre ellas, la imagen del abrazo que ahora circula descontextualizada (min. 00:06 aprox.):', 'URL': 'https://maldita.es/malditob

In [99]:
# This function "get_top_10_keywords" returns the top10 frequent words.
def get_top_10_keywords(words):
    """
    Return the top10 frequent words.
    :param list word: List containing all the words
    :return: ordered list with the top-10 most frequent words (in descending order)
    :rtype: list
    """
    counts = Counter(words)
    ordered_list = sorted(words, key=counts.get, reverse=True)
    unique_list = []
    
    #10 most common
    most_com = counts.most_common()[0:10]
    
    return most_com
    
    #El codigo de abajo devuelve una lista de tuplas con el numero de repeticiones de cada valor
    #for ol in ordered_list:
    #    if ol not in unique_list:
    #        unique_list.append(ol)
    #return unique_list[:10]

# This function "show_top_10_keywords" prints the top 10 words:

def show_top_10_keywords(processed_articles):
    # Show the top-10 most frequent words
    for article_words in processed_articles:
        # Get te top-10 words
        top_10_words = get_top_10_keywords(article_words)
        
        print("\nTOP 10 words:")
        for el in top_10_words:
            print(el[0], ':', el[1])

# Preprocessing

* Convierte el texto a minúscula
* Elimina los caracteres que no sean ASCII
* Quita signos de puntuación
* Quita las stopwords
* Se realiza la Lemmatizacion de los tokens
* Extrae las 10 palabras más frecuentes de los artículos

In [93]:
def to_lowercase(words):
    """Convert all characters to lowercase from list of tokenized words"""
    new_words = []
    for word in words:
        new_word = word.lower()
        new_words.append(new_word)
    return new_words

def remove_numbers(data):
    """Remove numbers"""
    articles = []
    for a in data:
        article = []
        for word in a:
            if not word.isdigit():
                article.append(word)
        articles.append(article)
    return articles


def remove_non_ascii(words):
    """Remove non-ASCII characters from list of tokenized words"""
    new_words = []
    for word in words:
        new_word = unicodedata.normalize('NFKD', word).encode('ascii', 'ignore').decode('utf-8', 'ignore')
        new_words.append(new_word)
    return new_words


def remove_punctuation(words):
    """Remove punctuation from list of tokenized words"""
    new_words = []
    for word in words:
        new_word = re.sub(r'[^\w\sÀ-ú]', '', word)
        if new_word != '':
            new_words.append(new_word)
    return new_words

def remove_stopwords_from_all_news(news, custom_stopwords):
    """
    Method to remove the stop words from a sentence.
    :param str sentence: List of all news
    :param list stopwords: List containing the stopwords to remove from the sentences
    :return: list of news with the stopwords removed
    :rtype: list
    """
    important_words_in_news=[]
    for one_news in news:
        new_words = []
        
        for word in one_news:
        # Only keep the important words
            if word not in custom_stopwords:
                new_words.append(word)         
        important_words_in_news.append(new_words)
        
    return important_words_in_news


In [100]:
def nlp_articles(articles):
    """
    Preprocesamiento:
        * Perform some normalization:
            -Convierte el texto a minúscula
            -Elimina los caracteres que no sean ASCII
            -Quita signos de puntuación
            -Quita las stopwords
            -Se realiza la Lemmatizacion de los tokens
            -Extrae las 10 palabras más frecuentes de los artículos
            
    :param list articles: List containing all the news we will process
    :return: list of news tokenized into words
    :rtype: list
    """
    print("PREPROCESSING...")
    print('articles len', len(articles[0]))
    print('articles len', len(articles[1]))
    
    # Lowercase all the articles
    lower_articles = to_lowercase(articles)
    print('lower len', len(lower_articles[0]))
    print('lower len', lower_articles[1])
    
    '''
    #ESTAS DOS SECCIONES ELIMINAN TILDES, CARACTERES RAROS E ICONOS
    
    accent_articles = remove_non_ascii(lower_articles)
    print('accent_articles len', len(accent_articles[0]))
    print('accent_articles len', accent_articles[1])
    
    #Remove the `` and '' and probably more useless stuff
    accent_articles2 = remove_punctuation(accent_articles)
    print('accent_articles2 len', len(accent_articles2[0]))
    print('accent_articles2 len', accent_articles2[1])
    '''
    
    #print('aaaaaaaaa',accent_articles2)
    
    '''
    #NLTK lemmatizer
    # Get the spanish lemmatizer
    lemmatizer = WordNetLemmatizer()
    lemmatized_articles = []
    for article in accent_articles2:
        article_words = []
        tokenized_article = nltk.word_tokenize(article)
        # The article contains all the words. Separate them
        for token in tokenized_article:
            article_words.append(lemmatizer.lemmatize(token))
        # The next step expects a string. Let's concatenate the separate words using blanks.
        lemmatized_articles.append(article_words)
        
    '''
    
    #SPACY lemmatizer
    nlp = spacy.load('es_core_news_sm')
    lemmatized_articles = []
    for article in accent_articles2:
        article_words = []
        doc = nlp(article)
        for token in doc:
            article_words.append(token.lemma_)
        lemmatized_articles.append(article_words)
     
        
    print('lemmatized len ', len(lemmatized_articles[0]))
    print('lemmatized len ', len(lemmatized_articles[1]))
    #print(lemmatized_articles[1])
    
    # Prepare our custom list of stopwords
    custom_stopwords = ["Noticia", "Noticias", "Parir", "Comer", "Bulo"]
    custom_stopwords += STOP_WORDS
    
    # Merging 2 stopwords lists
    for e in stopwords.words('spanish'):
        if e not in custom_stopwords:
            custom_stopwords.append(e)
    
    # Add all the punctuation signs to the list of stopwords
    custom_stopwords += list(string.punctuation)
    # lowercase all the stopwords
    my_stopwords = to_lowercase(custom_stopwords)
    
    articles_no_stopwords = remove_stopwords_from_all_news(lemmatized_articles, my_stopwords)
    print('articles_no_stopwords len', len(articles_no_stopwords[0]))
    print('articles_no_stopwords len', len(articles_no_stopwords[1]))
    
    articles_no_numbers = remove_numbers(articles_no_stopwords)
    
    return articles_no_numbers

# Obtengo las keywords
processed_articles = nlp_articles(content_list)

# Muestro las top-10 keywords
show_top_10_keywords(processed_articles)

PREPROCESSING...
articles len 3029
articles len 2196
lower len 3029
lower len circula por whatsapp una cadena en la que se dice que correos está "redondeando" los precios de sus servicios y que ese dinero se destina para "pagar mascarillas y elementos de protección para los funcionarios de correos". es un bulo: se trata de una campaña que han lanzado con el objetivo de recaudar fondos para la investigación contra la covid-19.desde correos nos explican que han "incorporado en la red de oficinas la figura del 'redondeo solidario' en su pasarela de pago, para ayudar a recaudar fondos y hacer frente al covid‐19". para ello, "los clientes de correos pueden redondear el importe final de su compra y donar los céntimos restantes a la lucha contra el coronavirus cada vez que utilicen su tarjeta como medio de pago".según correos, todo lo recaudado se destinará a "un proyecto conjunto de irsicaixa con el barcelona supercomputing center y el centro de investigación en sanidad animal del in

In [76]:
processed_articles

[['alarmar',
  'coronavirus',
  'circular',
  'foto',
  'vídeos',
  'animal',
  'campar',
  'ancho',
  'ciudad',
  'ciervo',
  'delfín',
  'flamenco',
  'supuestamente',
  'ocupar',
  'espaciar',
  'humano',
  'hemo',
  'dejar',
  'confinamiento',
  'embargar',
  'imágenes',
  'tipo',
  'semana',
  'habéis',
  'preguntar',
  'tomar',
  'crisis',
  'coronavirus',
  'montaje',
  'contar',
  'ejemplos.está',
  'circular',
  'vídeo',
  'redar',
  'social',
  'aparecer',
  'delfín',
  'nadar',
  'puerto',
  'deportivo',
  'supuestamente',
  'deber',
  'inactividad',
  'puerto',
  'provocar',
  'crisis',
  'sanitario',
  'coronavirus',
  'vídeo',
  'mover',
  'tratar',
  'pasear',
  'marítimo',
  'palmar',
  'mallorca',
  'puerto',
  'denia',
  'alicante',
  'moraira',
  'alicante',
  'premià',
  'mar',
  'barcelona',
  'imágenes',
  'grabar',
  'puerto',
  'deportivo',
  'ataköy',
  'ciudad',
  'estambul',
  'turquía',
  'contar',
  'aquí.nos',
  'estáis',
  'preguntar',
  'ví

In [67]:
print(dataset[1])

{'Title': 'No, Correos no está "redondeando" sus precios con tal de comprar mascarillas para sus trabajadores: los fondos son para la investigación contra la COVID-19', 'Publication_date': '24/05/2020', 'Content': 'Circula por WhatsApp una cadena en la que se dice que Correos está "redondeando" los precios de sus servicios y que ese dinero se destina para "pagar mascarillas y elementos de protección para los funcionarios de Correos". Es un bulo: se trata de una campaña que han lanzado con el objetivo de recaudar fondos para la investigación contra la COVID-19.Desde Correos nos explican que han "incorporado en la red de oficinas la figura del \'redondeo solidario\' en su pasarela de pago, para ayudar a recaudar fondos y hacer frente al COVID‐19". Para ello, "los clientes de Correos pueden redondear el importe final de su compra y donar los céntimos restantes a la lucha contra el coronavirus cada vez que utilicen su tarjeta como medio de pago".Según Correos, todo lo recaudado se de

In [68]:
#TfidfVectorizer will L-2 normalize the output matrix by default, as a final step of the calculation. Having it normalized 
#means it will have only weights between 0 and 1.

vectorizer = TfidfVectorizer(preprocessor=lambda x: x, tokenizer=lambda x: x, norm='l2')
tfidf_matrix = vectorizer.fit_transform(processed_articles)

#TfidfVectorizer ---> Equivalent to CountVectorizer followed by TfidfTransformer.
#idfs are calculated by TfidfTransformer's fit()
#tfidfs are calculated by TfidfTransformer's transform()
#tfs are calculated by CountVectorizer's fit_transform()

matrix_vocab = vectorizer.get_feature_names()
matrix = tfidf_matrix.todense()
#matrix_idf = vectorizer.idf_
print(tfidf_matrix.shape)
print(matrix_vocab)
#print(matrix[43])

#Posicion numero 36 -> 35 en la lista "Barcelona" aparece en ambos vectores de tf idf. La palabra aparece en los 2 documentos. 
#En el primero 2 veces y en el 2º 1 vez.
#En el primero hay 2 barcelonas-> 0,06 y en el segundo 1 barcelona -> 0,04

(1224, 20992)
['\n', '\r', ' ', '  ', '   ', '    ', '      ', '          ', '001el', '0042de', '044578433ademas', '0548pero', '0i', '0ms', '0quedateencasa', '1000cuando', '100el', '100o', '102la', '10440de', '104en', '105asi', '1072tampoco', '10el', '10h', '10k', '10n', '10news', '10th', '112no', '1130h', '116en', '117la', '1183aunque', '11asturias', '11s', '120o', '1221h', '123mientras', '1240am', '1247pm', '124pm', '12721iglesias', '12clm', '12h', '12minutoscom', '12minutoscoma', '12minutoscomla', '1303datosmetroel', '130o', '132secuencia', '13asturias', '13c', '13en', '13este', '144am', '1463por', '14cataluna', '14la', '14por', '14segun', '1500472sic', '1500en', '1521esas', '158ademas', '15912009la', '15cyl', '15h', '15por', '1604h', '1640en', '165000un', '1652el', '174navarra', '17a', '17cantabria', '17h', '180infocouk', '180no', '1831en', '1839por', '185k', '18cantabria', '18si', '18th', '1920ademas', '1927contactada', '1945h', '1958malditaes', '1975en', '1992os', '19th', '1helic

In [69]:
import numpy as np
import sys
np.set_printoptions(threshold=1000) #sys.maxsize
matrix[43]

matrix([[0., 0., 0., ..., 0., 0., 0.]])

In [70]:
print(matrix.shape)
print('video - 8:', matrix_vocab.index("video"))
print('correos - 9:', matrix_vocab.index("correo"))
print('puerto - 5:', matrix_vocab.index("puerto"))
print('bulo - 5:', matrix_vocab.index("bulo"))

#Por que bulo tiene menos valor de tf idf si sale las mismas veces en 1 mismo doc y sale 1 vez en el 2º doc mientras que puerto no sale en el 2 doc
video = matrix_vocab.index("video")
correos = matrix_vocab.index("correo")
puerto = matrix_vocab.index("puerto")
bulo = matrix_vocab.index("bulo")

(1224, 20992)
video - 8: 20330
correos - 9: 5048
puerto - 5: 16231


ValueError: 'bulo' is not in list

In [ ]:
A = np.asarray(matrix[1]).reshape(-1)
print(A[video])
print(A[correos])
print(A[puerto])
print(A[bulo])

TF IDF mide la "importancia" de las palabras. Palabras que salen mucho tienen el tf idf mas bajo pero tambien lo tienen mas veces porque salen en mas documentos. Por otro lado las que salen menos como "ornitorrinco" tendrian un TF IDF más alto pero único puesto que salen en pocos documentos pero son palabras que caracterizan un documento en concreto

In [ ]:
'''
from sklearn.feature_extraction.text import TfidfVectorizer
corpus = ['bulo bulo hola hola.',
            'bulo ornitorrinco']
vect = TfidfVectorizer()
X = vect.fit_transform(corpus)
matrix_vocab = vect.get_feature_names()
print(matrix_vocab)
X.todense()
'''

### CLUSTERING SECTION

* Clusterización empleando MiniBatchKMeans puesto que su ejecución es mas rápida y los resultados son muy similares al Kmeans.
* Método del codo -> Buscamos el número óptimo de clusters en base al SSE. Nos quedamos con el número de clusters más óptimo y más visual para el análisis.
* Dibujamos los clusters en base al PCA y al TSNE.
* Mostramos el top keywords de cada cluster.

In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib.cm as cm

from sklearn.cluster import MiniBatchKMeans, KMeans
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE

sum of squared errors (SSE) - SSE is the sum of the squared differences between each observation and its group's mean. It can be used as a measure of variation within a cluster. If all cases within a cluster are identical the SSE would then be equal to 0.

In [ ]:
def find_optimal_clusters(data, max_k):
    iters = range(2, max_k+1, 2)
    
    sse = []
    for k in iters:
        sse.append(MiniBatchKMeans(n_clusters=k, init_size=1024, batch_size=2048, random_state=20).fit(data).inertia_)
        print('Fit {} clusters'.format(k))
        
    f, ax = plt.subplots(1, 1)
    ax.plot(iters, sse, marker='o')
    ax.set_xlabel('Cluster Centers')
    ax.set_xticks(iters)
    ax.set_xticklabels(iters)
    ax.set_ylabel('SSE')
    ax.set_title('SSE by Cluster Center Plot')
    
find_optimal_clusters(tfidf_matrix, 30)

In [ ]:
from IPython.display import Image
Image(filename='elbow1.png')

In [ ]:
clusters = MiniBatchKMeans(n_clusters=12, init_size=1024, batch_size=2048, random_state=20).fit_predict(tfidf_matrix)

PCA = análisis de componentes principales : Es un algoritmo de reducción de dimensionalidad que permite la visualización en 2 o 3 dimensiones de conjuntos de datos de un mayor número de dimensiones

TSNE = t-Distributed Stochastic Neighbor Embedding (t-SNE) is a technique for dimensionality reduction that is particularly well suited for the visualization of high-dimensional datasets.

https://www.interactivechaos.com/manual/tutorial-de-machine-learning/t-sne

t-SNE (T-distributed Stochastic Neighbor Embedding) es un algoritmo diseñado para la visualización de conjuntos de datos de alta dimensionalidad. Si el número de dimensiones es muy alto, Scikit-Learn recomienda en su documentación utilizar un método de reducción de dimensionalidad previo (como PCA) para reducir el conjunto de datos a un número de dimensiones razonable (por ejemplo 50), lo que reducirá el ruido y aligerará la ejecución de t-SNE.

In [ ]:
def plot_tsne_pca(data, labels):
    max_label = max(labels)
    max_items = np.random.choice(range(data.shape[0]), size=3000, replace=True)
    
    pca = PCA(n_components=2).fit_transform(data[max_items,:].todense())
    tsne = TSNE().fit_transform(PCA(n_components=50).fit_transform(data[max_items,:].todense()))
    
    
    idx = np.random.choice(range(pca.shape[0]), size=300, replace=False)
    label_subset = labels[max_items]
    label_subset = [cm.hsv(i/max_label) for i in label_subset[idx]]
    
    f, ax = plt.subplots(1, 2, figsize=(14, 6))
    
    ax[0].scatter(pca[idx, 0], pca[idx, 1], c=label_subset)
    ax[0].set_title('PCA Cluster Plot')
    
    ax[1].scatter(tsne[idx, 0], tsne[idx, 1], c=label_subset)
    ax[1].set_title('TSNE Cluster Plot')
    
plot_tsne_pca(tfidf_matrix, clusters)

In [ ]:
def get_top_keywords(data, clusters, labels, n_terms):
    df = pd.DataFrame(data.todense()).groupby(clusters).mean()
    #display(df)
    #I=Number for row, r=content of dataframe
    for i,r in df.iterrows():
        print('\nCluster {}'.format(i))
        #print(np.argsort(r)[-n_terms:])
        #print(labels[18109])
        #print(labels[18239])
        #print(labels[18228])  
        print(','.join([labels[t] for t in np.argsort(r)[-n_terms:]]))
            
get_top_keywords(tfidf_matrix, clusters, matrix_vocab, 10)

Se puede asumir que mensaje y mensajes son clasificadas diferente porque el lematizador diferencia entre verbos y nombres -> mensajear != mensaje/mensajes

Debo quitar palabra como The, ma , sm en las stopwords ya que es ruido? o lo tengo que dejar para ver que también hay ciertos "errores"